In [319]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit

In [320]:
from BHDVCS import BHDVCS
bhdvcs = BHDVCS()
total_uuxs = bhdvcs.TotalUUXS_curve_fit

### Utility functions

In [321]:
def chi2overdof(y, yhat, err): # accepts list or 1d-array or Series (assumes 3 parameters)
    assert len(y) == len(yhat) == len(err)
    
    if type(y) == pd.core.series.Series:
        y = y.reset_index(drop=True)

    if type(yhat) == pd.core.series.Series:
        yhat = yhat.reset_index(drop=True)
    
    if type(err) == pd.core.series.Series:
        err = err.reset_index(drop=True)

    n = len(y)
    cumsum = 0
    for i in range(n):
        cumsum += ((y[i] - yhat[i])/err[i])**2
    return cumsum/(n-3)

In [322]:
def phiparswcff(sect, cff=None):
    if cff is not None:
        pars = df.loc[sect, ['QQ', 'x_b', 't', 'k', 'F1', 'F2']]
        pars['ReH'] = cff[0]
        pars['ReE'] = cff[1]
        pars['ReHTilde'] = cff[2]
    else:
        pars = df.loc[sect, ['QQ', 'x_b', 't', 'k', 'F1', 'F2', 'ReH', 'ReE', 'ReHTilde']]
    pars['const'] = 0.014863
    phis = df.loc[sect, 'phi_x']
    phis = phis.reset_index(drop=True)
    pars = pars.reset_index(drop=True)
    return phis, pars

In [323]:
def findfs(phis, pars):
    fs_g_pars = []
    for j in range(36):
        fs_g_pars.append(bhdvcs.TotalUUXS([phis[j]], pars.loc[j, :])) 
    return fs_g_pars

In [324]:
df = pd.read_csv('DVCS_cross_6%.csv')

In [325]:
df = df.drop('#Index', axis='columns')

In [326]:
df.index = np.asarray(list(range(720))) // 36

In [327]:
sn = 2
X = (df.loc[sn, 'phi_x'], df.loc[sn, 'QQ'], df.loc[sn, 'x_b'], df.loc[sn, 't'], df.loc[sn, 'k'], df.loc[sn, 'dvcs'])

## Unbounded fit (levenberg-marquardt)

In [328]:
y = df.loc[sn, 'F']
sigma = df.loc[sn, 'errF']
pars0 = np.array([0, 0, 0]) #starting guesses for the parameters ReH, ReE, ReHTilde (in that order)

In [329]:
cff, cffcov = curve_fit(total_uuxs, X, y, pars0, sigma, method='lm')

In [330]:
perr = np.sqrt(np.diag(cffcov))

In [331]:
pd.DataFrame({'Fitted': cff,
              'Correct':df.iloc[0, :][['ReH', 'ReE', 'ReHTilde']].values,
              'EstError': perr},
             ['ReH', 'ReE', 'ReHTilde'])

Fitted   Correct  EstError
ReH       0.481987   2.56990  0.044986
ReE       1.042246 -15.18220  0.129844
ReHTilde -0.843926   1.63932  0.930847

### With all sets

In [332]:
(cff - correct)/correct

array([-0.81244906, -1.06864923, -1.51480231])

In [333]:
phis, pars = phiparswcff(sn, cff)
fs_g_pars = []
for j in range(36):
    fs_g_pars.append(bhdvcs.TotalUUXS([phis[j]], pars.loc[j, :])) 

In [334]:
chi2overdof(df.loc[sn, 'F'], fs_g_pars, df.loc[sn, 'errF'])

3.424646034993401

In [335]:
allsets = pd.DataFrame({'Index':[], 'Fitted':[], 'Correct':[], 'EstError':[], 'PctError':[], 'Chi2':[]})
for i in range(20):
    X = (df.loc[i, 'phi_x'], df.loc[i, 'QQ'], df.loc[i, 'x_b'], df.loc[i, 't'], df.loc[i, 'k'], df.loc[i, 'dvcs'])
    y = df.loc[i, 'F']
    sigma = df.loc[i, 'errF']
    pars0 = np.array([0, 0, 0])
    
    cff, cffcov = curve_fit(total_uuxs, X, y, pars0, sigma, method='lm', maxfev=5000)
    perr = np.sqrt(np.diag(cffcov))
    correct = df.iloc[i, :][['ReH', 'ReE', 'ReHTilde']].values
    pcterr = np.round(100*(cff - correct)/correct, decimals=2)
    
    phis, pars = phiparswcff(i, cff) #parameters to feed uuxs
    
    fs_g_pars = []
    for j in range(36):
        fs_g_pars.append(bhdvcs.TotalUUXS([phis[j]], pars.loc[j, :])) #calculate uuxs with params
        
    chi2 = chi2overdof(df.loc[i, 'F'], fs_g_pars, df.loc[i, 'errF'])
    
    this = pd.DataFrame({'Index': [i, i, i],
              'Fitted': cff,
              'Correct': df.iloc[0, :][['ReH', 'ReE', 'ReHTilde']].values,
              'EstError': perr,
              'PctError': pcterr,
              'Chi2': chi2},
             ['ReH', 'ReE', 'ReHTilde'])
    allsets = allsets.append(this)

### Formatted Results

In [336]:
allsets.round(2)

Index   Fitted  Correct      EstError   PctError       Chi2
ReH         0.0     0.95     2.57  2.000000e-02     -63.05      26.70
ReE         0.0     0.03   -15.18  2.000000e-01    -100.17      26.70
ReHTilde    0.0    10.18     1.64  4.040000e+00     521.29      26.70
ReH         1.0     0.67     2.57  3.000000e-02     -73.78       4.66
ReE         1.0     0.79   -15.18  1.300000e-01    -105.20       4.66
ReHTilde    1.0     1.62     1.64  1.320000e+00      -1.16       4.66
ReH         2.0     0.48     2.57  4.000000e-02     -81.24       3.42
ReE         2.0     1.04   -15.18  1.300000e-01    -106.86       3.42
ReHTilde    2.0    -0.84     1.64  9.300000e-01    -151.48       3.42
ReH         3.0     0.46     2.57  5.000000e-02     -82.29       3.30
ReE         3.0     0.97   -15.18  1.400000e-01    -106.40       3.30
ReHTilde    3.0    -1.24     1.64  8.800000e-01    -175.92       3.30
ReH         4.0     0.46     2.57  4.000000e-02     -81.96       2.36
ReE         4.0     0.76   -15.18  1.400000e-01    -105.03       2.36
ReHTilde    4.0    -1.08     1.64  8.600000e-01    -165.58       2.36
ReH         5.0     0.76     2.57  4.000000e-02     -70.24      10.63
ReE         5.0     0.93   -15.18  1.200000e-01    -106.10      10.63
ReHTilde    5.0    -2.53     1.64  1.230000e+00    -254.59      10.63
ReH         6.0     0.57     2.57  4.000000e-02     -77.94       7.70
ReE         6.0     1.13   -15.18  1.000000e-01    -107.44       7.70
ReHTilde    6.0    -1.23     1.64  8.800000e-01    -175.32       7.70
ReH         7.0     0.37     2.57  5.000000e-02     -85.57      16.93
ReE         7.0     1.30   -15.18  1.100000e-01    -108.59      16.93
ReHTilde    7.0    -1.02     1.64  6.800000e-01    -161.96      16.93
ReH         8.0     0.31     2.57  8.000000e-02     -87.99      25.33
ReE         8.0     1.24   -15.18  1.400000e-01    -108.13      25.33
ReHTilde    8.0     0.62     1.64  8.200000e-01     -62.01      25.33
ReH         9.0     0.34     2.57  5.000000e-02     -86.81      41.07
ReE         9.0     1.04   -15.18  1.000000e-01    -106.87      41.07
ReHTilde    9.0    -0.64     1.64  5.500000e-01    -138.79      41.07
ReH        10.0     1.13     2.57  1.953000e+01     -55.95  415365.49
ReE        10.0    -1.13   -15.18  3.620000e+02     -92.56  415365.49
ReHTilde   10.0 -2249.66     1.64  3.851151e+08 -137331.27  415365.49
ReH        11.0     0.95     2.57  2.000000e-02     -62.92      23.02
ReE        11.0    -0.28   -15.18  2.500000e-01     -98.13      23.02
ReHTilde   11.0     5.68     1.64  4.440000e+00     246.54      23.02
ReH        12.0     0.67     2.57  4.000000e-02     -74.04       5.82
ReE        12.0     0.58   -15.18  1.600000e-01    -103.83       5.82
ReHTilde   12.0     2.17     1.64  1.640000e+00      32.12       5.82
ReH        13.0     0.51     2.57  4.000000e-02     -80.28       2.44
ReE        13.0     0.89   -15.18  1.100000e-01    -105.89       2.44
ReHTilde   13.0    -1.99     1.64  7.200000e-01    -221.31       2.44
ReH        14.0     0.48     2.57  3.000000e-02     -81.14       2.05
ReE        14.0     0.75   -15.18  9.000000e-02    -104.95       2.05
ReHTilde   14.0    -1.98     1.64  5.800000e-01    -221.04       2.05
ReH        15.0     0.76     2.57  4.000000e-02     -70.55      12.94
ReE        15.0     0.95   -15.18  1.200000e-01    -106.28      12.94
ReHTilde   15.0    -1.73     1.64  1.310000e+00    -205.83      12.94
ReH        16.0     0.33     2.57  8.000000e-02     -87.28      13.70
ReE        16.0     1.60   -15.18  1.400000e-01    -110.52      13.70
ReHTilde   16.0    -1.98     1.64  8.400000e-01    -220.90      13.70
ReH        17.0     0.11     2.57  1.441275e+05     -95.72     169.21
ReE        17.0     1.39   -15.18  1.441278e+05    -109.18     169.21
ReHTilde   17.0     3.22     1.64  3.220000e+00      96.34     169.21
ReH        18.0     0.11     2.57  9.792900e+02     -95.58     153.81
ReE        18.0     1.24   -15.18  9.790900e+02    -108.14     153.81
ReHTilde   18.0     

### Compare Chi2 with actual values

In [337]:
for i in range(20):
    phis, pars = phiparswcff(i)
    fs_g_pars = findfs(phis, pars)
    print(i, chi2overdof(df.loc[i, 'F'], fs_g_pars, df.loc[i, 'errF']))

0 2.6424145073369147
1 4.877698551581844
2 3.0309819328867165
3 2.5838718422514426
4 1.953491915361266
5 7.3504634319186755
6 7.082708366663117
7 13.466550114184047
8 20.472811189641874
9 35.564073461288935
10 12.509368118803067
11 7.8155382529856
12 3.915149373518586
13 3.227257842234303
14 2.5937887640836284
15 9.208748915294322
16 5.467320297370923
17 4.868204683904224
18 8.563972394610778
19 33.50516324052611


### Pct within 2 stds

In [174]:
np.mean(((allsets['Fitted'] - allsets['EstError']*2) < allsets['Correct']) & ((allsets['Fitted'] + allsets['EstError']*2) > allsets['Correct']))

0.7166666666666667

### Avg PctErr

For all

In [80]:
np.median(np.abs(allsets['PctError']))

101.94

For each index

In [88]:
perIndex = []
for i in range(20):
    perIndex.append(np.mean(np.abs(allsets.loc[allsets['Index'] == i, 'PctError'])))
perIndex = pd.Series(perIndex)

In [95]:
perIndex.sort_values()

1        69.733333
16       71.843333
12       73.003333
6        82.223333
3        90.980000
7        93.726667
13       99.606667
15      102.286667
2       105.380000
14      118.016667
5       143.946667
17      158.893333
4       164.003333
8       180.386667
0       228.170000
18      246.763333
9       277.516667
19      366.493333
11     1756.710000
10    89388.030000
dtype: float64

For each parameter

In [103]:
np.abs(allsets['PctError']).groupby(level=0).mean()

ReE           110.099
ReH            79.211
ReHTilde    13883.347
Name: PctError, dtype: float64

In [104]:
np.abs(allsets['PctError']).groupby(level=0).median()

ReE         112.555
ReH          89.105
ReHTilde    205.130
Name: PctError, dtype: float64

### Bounded

In [106]:
allsets = pd.DataFrame({'Index':[], 'Fitted':[], 'Correct':[], 'EstError':[], 'PctError':[]})
for i in range(20):
    X = (df.loc[i, 'phi_x'], df.loc[i, 'QQ'], df.loc[i, 'x_b'], df.loc[i, 't'], df.loc[i, 'k'], df.loc[i, 'dvcs'])
    y = df.loc[sn, 'F']
    sigma = df.loc[sn, 'errF']
    pars0 = np.array([0, 0, 0])
    
    cff, cffcov = curve_fit(total_uuxs, X, y, pars0, sigma, bounds=(-100, 100), maxfev=5000)
    perr = np.sqrt(np.diag(cffcov))
    correct = df.iloc[i, :][['ReH', 'ReE', 'ReHTilde']].values
    pcterr = np.round(100*(cff - correct)/correct, decimals=2)
    
    this = pd.DataFrame({'Index': [i, i, i],
              'Fitted': cff,
              'Correct': df.iloc[0, :][['ReH', 'ReE', 'ReHTilde']].values,
              'EstError': perr,
              'PctError': pcterr},
             ['ReH', 'ReE', 'ReHTilde'])
    allsets = allsets.append(this)

In [107]:
allsets

Index      Fitted   Correct     EstError  PctError
ReH         0.0    0.949673   2.56990     0.024641    -63.05
ReE         0.0    0.025321 -15.18220     0.198478   -100.17
ReHTilde    0.0   10.184868   1.63932     4.038968    521.29
ReH         1.0    0.816262   2.56990     0.041775    -68.24
ReE         1.0    1.341461 -15.18220     0.135745   -108.84
ReHTilde    1.0    2.165896   1.63932     1.270900     32.12
ReH         2.0    0.406841   2.56990     0.151036    -84.17
ReE         2.0    2.299966 -15.18220     0.233068   -115.15
ReHTilde    2.0   -0.275777   1.63932     0.968482   -116.82
ReH         3.0    0.231278   2.56990  1384.359919    -91.00
ReE         3.0    2.520995 -15.18220  1384.493609   -116.60
ReHTilde    3.0    2.708523   1.63932     1.607512     65.22
ReH         4.0    0.250414   2.56990  2405.118513    -90.26
ReE         4.0    2.376451 -15.18220  2405.373968   -115.65
ReHTilde    4.0    6.323928   1.63932     3.169477    285.77
ReH         5.0    0.899064   2.56990     0.038906    -65.02
ReE         5.0    0.562603 -15.18220     0.156176   -103.71
ReHTilde    5.0    5.952464   1.63932     2.356846    263.11
ReH         6.0    0.561537   2.56990     0.076420    -78.15
ReE         6.0    1.770976 -15.18220     0.156645   -111.66
ReHTilde    6.0    0.707194   1.63932     1.255109    -56.86
ReH         7.0    0.188029   2.56990  1345.883701    -92.68
ReE         7.0    2.372781 -15.18220  1345.987912   -115.63
ReHTilde    7.0    2.832296   1.63932     1.607568     72.77
ReH         8.0    0.212846   2.56990  3223.368368    -91.72
ReE         8.0    2.305925 -15.18220  3223.570267   -115.19
ReHTilde    8.0    7.113179   1.63932     3.202785    333.91
ReH         9.0    0.231401   2.56990  3561.881194    -91.00
ReE         9.0    2.190844 -15.18220  3561.541723   -114.43
ReHTilde    9.0   11.906539   1.63932     5.709963    626.31
ReH        10.0    1.500010   2.56990     0.358997    -41.63
ReE        10.0   -1.355455 -15.18220    13.679964    -91.07
ReHTilde   10.0 -100.000000   1.63932  9611.381472  -6200.09
ReH        11.0    1.480672   2.56990     0.044927    -42.38
ReE        11.0   -1.246425 -15.18220     1.518190    -91.79
ReHTilde   11.0   85.795334   1.63932   588.244399   5133.59
ReH        12.0    1.034381   2.56990     0.056005    -59.75
ReE        12.0    1.497596 -15.18220     0.174790   -109.86
ReHTilde   12.0    2.449157   1.63932     1.517944     49.40
ReH        13.0    0.267785   2.56990   806.394550    -89.58
ReE        13.0    2.911185 -15.18220   806.298611   -119.17
ReHTilde   13.0    0.162532   1.63932     1.115079    -90.09
ReH        14.0    0.292147   2.56990  2158.755977    -88.63
ReE        14.0    2.773383 -15.18220  2158.578366   -118.27
ReHTilde   14.0    4.049003   1.63932     2.123792    146.99
ReH        15.0    0.731392   2.56990     0.036881    -71.54
ReE        15.0    0.893265 -15.18220     0.123308   -105.88
ReHTilde   15.0    3.761206   1.63932     1.638279    129.44
ReH        16.0    0.136568   2.56990   938.073961    -94.69
ReE        16.0    2.082286 -15.18220   938.000574   -113.72
ReHTilde   16.0    1.521237   1.63932     1.162068     -7.20
ReH        17.0    0.157195   2.56990  1382.557438    -93.88
ReE        17.0    1.991660 -15.18220  1382.386717   -113.12
ReHTilde   17.0    6.054826   1.63932     2.765689    269.35
ReH        18.0    0.167400   2.56990  1760.681695    -93.49
ReE        18.0    1.819925 -15.18220  1760.373822   -111.99
ReHTilde   18.0   10.391535   1.63932     5.276163    533.89
ReH        19.0    0.175502   2.56990  3184.146102    -93.17
ReE        19.0    1.666196 -15.18220  3183.642406   -110.97
ReHTilde   19.0   16.283179   1.63932     9.812382    893.29

### Pct within 2 stds

In [108]:
np.mean(((allsets['Fitted'] - allsets['EstError']*2) < allsets['Correct']) & ((allsets['Fitted'] + allsets['EstError']*2) > allsets['Correct']))

0.7

### Avg PctError

In [109]:
np.median(np.abs(allsets['PctError']))

101.94

In [110]:
perIndex = []
for i in range(20):
    perIndex.append(np.mean(np.abs(allsets.loc[allsets['Index'] == i, 'PctError'])))
perIndex = pd.Series(perIndex)

In [111]:
perIndex.sort_values()

1       69.733333
16      71.870000
12      73.003333
6       82.223333
3       90.940000
7       93.693333
13      99.613333
15     102.286667
2      105.380000
14     117.963333
5      143.946667
17     158.783333
4      163.893333
8      180.273333
0      228.170000
18     246.456667
9      277.246667
19     365.810000
11    1755.920000
10    2110.930000
dtype: float64

In [112]:
np.abs(allsets['PctError']).groupby(level=0).mean()

ReE         110.1435
ReH          79.2015
ReHTilde    791.3755
Name: PctError, dtype: float64